# VAE Approach

In [1]:
import warnings
warnings.filterwarnings('ignore')

In [2]:
from ocpa.objects.log.importer.ocel import factory as ocel_import_factory
from ocpa.algo.conformance.precision_and_fitness import evaluator as quality_measure_factory
from ocpa.algo.discovery.ocpn import algorithm as ocpn_discovery_factory
from src.utils import get_happy_path_log, create_flower_model, generate_variant_model, sample_traces, process_log
from ocpa.objects.log.importer.csv import factory as ocel_import_factory_csv
from models.VAE_measure import get_text_data, decode_sequence, create_lstm_vae, VAE_generalization

In [3]:
from tensorflow.python.framework.ops import disable_eager_execution
disable_eager_execution()

In [4]:
import argparse
import json
from keras import backend as K
from keras.losses import categorical_crossentropy
from keras.layers import Layer
from keras.layers import Input, LSTM, TimeDistributed
from keras.layers.core import Dense, Lambda
from keras.models import Model
from nltk.tokenize import word_tokenize
import tensorflow as tf
import pandas as pd
import numpy as np
import codecs
import os, re
from tqdm import tqdm
import random
from datetime import datetime, timedelta
import time

In [7]:
filename = "../src/data/jsonocel/order_process.jsonocel"
ocel = ocel_import_factory.apply(filename)
ocpn = ocpn_discovery_factory.apply(ocel, parameters={"debug": False})
train_log = sample_traces(ocel, ocpn, 10000, save_path='../src/data/playout/ocpn_data_order.txt')


Generate the traces: 100%|██████████| 10000/10000 [00:00<00:00, 29646.00it/s]


In [20]:
# # Open the file in read mode
# file = open(data_path, "r")

# # Read the file line by line and split into words
# lines = file.readlines()
# file.close()

# # Process each line and store words in a list of lists
# train_log = []
# for line in lines:
#     words = line.lower().strip().split()
#     line = " ".join(words)
#     train_log.append(line)

In [21]:
train_log

['place order confirm order item out of stock fuel car reorder item pick item payment reminder pay order load cargo start route end route',
 'fuel car place order confirm order payment reminder payment reminder item out of stock reorder item pay order pick item load cargo start route end route',
 'fuel car place order confirm order payment reminder pick item payment reminder payment reminder load cargo pay order start route end route',
 'place order fuel car confirm order pick item payment reminder load cargo item out of stock reorder item pay order pick item load cargo start route end route',
 'fuel car place order confirm order payment reminder pick item load cargo payment reminder start route pay order item out of stock end route',
 'fuel car place order confirm order pick item load cargo pay order item out of stock reorder item start route end route',
 'place order fuel car confirm order item out of stock pay order reorder item pick item load cargo start route end route',
 'place o

In [16]:
timesteps_max, enc_tokens, characters, char2id, id2char, x, x_decoder = get_text_data(num_samples=10000,
                                                                                      data_path='../src/data/playout/ocpn_data_order.txt')

print(x.shape, "Creating model...")

Number of samples: 10000
Number of unique input tokens: 21
Max sequence length for inputs: 52
(10000, 52, 21) Creating model...


In [21]:
input_dim, timesteps = x.shape[-1], x.shape[-2]
batch_size, latent_dim = 1, 191
intermediate_dim, epochs = 353, 10

vae, enc, gen, stepper = create_lstm_vae(input_dim,
                                         batch_size=batch_size,
                                         intermediate_dim=intermediate_dim,
                                         latent_dim=latent_dim,
                                        )
print("Training model...")

vae.fit([x, x_decoder], x, epochs=epochs, verbose=1)

Model: "model_20"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_26 (InputLayer)          [(None, None, 21)]   0           []                               
                                                                                                  
 lstm_10 (LSTM)                 (None, 353)          529500      ['input_26[0][0]']               
                                                                                                  
 dense_20 (Dense)               (None, 191)          67614       ['lstm_10[0][0]']                
                                                                                                  
 dense_21 (Dense)               (None, 191)          67614       ['lstm_10[0][0]']                
                                                                                           

In [26]:
print("Fitted, predicting...")

def decode(s):
    return decode_sequence(s, gen, stepper, input_dim, char2id, id2char, timesteps_max)

log = []

for _ in tqdm(range(10000), desc="Sample Traces"):

    id_from = np.random.randint(0, x.shape[0] - 1)
    id_to = np.random.randint(0, x.shape[0] - 1)

    m_from, std_from = enc.predict([[x[id_from]]])
    m_to, std_to = enc.predict([[x[id_to]]])

    seq_from = np.random.normal(size=(latent_dim,))
    seq_from = m_from + std_from * seq_from

    seq_to = np.random.normal(size=(latent_dim,))
    seq_to = m_to + std_to * seq_to

    print("==  \t", " ".join([id2char[j] for j in np.argmax(x[id_from], axis=1)]), "==")

    for v in np.linspace(0, 1, 7):
        print("%.2f\t" % (1 - v), decode(v * seq_to + (1 - v) * seq_from))

    print("==  \t", " ".join([id2char[j] for j in np.argmax(x[id_to], axis=1)]), "==")
    parts = " ".join([id2char[j] for j in np.argmax(x[id_to], axis=1)]).split(' <end>')
    log.append([parts[0]])

Fitted, predicting...


Sample Traces: 100%|██████████| 10000/10000 [04:52<00:00, 34.23it/s]


In [27]:
log

[['fuel car place order confirm order pay order item out of stock pick item reorder item pick item load cargo start route end route'],
 ['place order confirm order item out of stock pay order pick item load cargo reorder item fuel car start route pick item load cargo end route'],
 ['fuel car place order confirm order pay order item out of stock reorder item pick item load cargo start route end route'],
 ['fuel car place order confirm order pay order item out of stock pick item reorder item load cargo pick item start route end route'],
 ['place order confirm order pick item pay order fuel car load cargo item out of stock start route reorder item pick item load cargo start route end route'],
 ['place order confirm order payment reminder payment reminder item out of stock reorder item pick item pay order load cargo fuel car start route end route'],
 ['place order fuel car confirm order pick item load cargo pay order item out of stock start route end route'],
 ['fuel car place order confir

In [10]:
# data_path_gen = '../src/data/VAE_generated/gen_data_order.txt'

In [11]:
# with open(data_path_gen, "w", encoding="utf-8") as file:
#     for sentence in log:
#         line = " ".join(sentence) + "\n"
#         file.write(line)

In [12]:
# # Open the file in read mode
# file = open(data_path_gen, "r")

# # Read the file line by line and split into words
# lines = file.readlines()
# file.close()

# # Process each line and store words in a list of lists
# gen_log = []
# for line in lines:
#     words = line.lower().strip().split()
#     line = " ".join(words)
#     gen_log.append([line])

In [13]:
gen_log

[['fuel car place order confirm order pay order item out of stock pick item reorder item pick item load cargo start route end route'],
 ['place order confirm order item out of stock pay order pick item load cargo reorder item fuel car start route pick item load cargo end route'],
 ['fuel car place order confirm order pay order item out of stock reorder item pick item load cargo start route end route'],
 ['fuel car place order confirm order pay order item out of stock pick item reorder item load cargo pick item start route end route'],
 ['place order confirm order pick item pay order fuel car load cargo item out of stock start route reorder item pick item load cargo start route end route'],
 ['place order confirm order payment reminder payment reminder item out of stock reorder item pick item pay order load cargo fuel car start route end route'],
 ['place order fuel car confirm order pick item load cargo pay order item out of stock start route end route'],
 ['fuel car place order confir

In [14]:
df_log = process_log(gen_log, ocel, ocpn, '../src/data/VAE_generated/gen_data_order.csv')

In [15]:
df_log

event_id     event_activity  event_execution  \
0              0           Fuel Car                1   
1              1        Place Order                1   
2              2      Confirm Order                1   
3              3          Pay Order                1   
4              4  Item out of stock                1   
...          ...                ...              ...   
114632    114632           Fuel Car            10000   
114633    114633  Item out of stock            10000   
114634    114634         Load Cargo            10000   
114635    114635        Start Route            10000   
114636    114636          End Route            10000   

                   event_timestamp         delivery     order         item  
0       2022-01-01 14:19:28.781792      [delivery1]        []           []  
1       2022-01-01 14:20:28.781792               []  [order1]      [item1]  
2       2022-01-01 14:21:28.781792               []  [order1]      [item1]  
3       2022-01-01 14:22:28.781792               []  [order1]           []  
4       2022-01-01 14:23:28.781792               []        []      [item1]  
...                            ...              ...       ...          ...  
114632  2025-02-19 05:25:11.254791  [delivery10000]        []           []  
114633  2025-02-19 05:26:11.254791               []        []  [item10000]  
114634  2025-02-19 05:27:11.254791  [delivery10000]        []  [item10000]  
114635  2025-02-19 05:28:11.254791  [delivery10000]        []  [item10000]  
114636  2025-02-19 05:29:11.254791  [delivery10000]        []  [item10000]  

[114637 rows x 7 columns]

In [8]:
object_types = ["order","item","delivery"]
parameters = {"obj_names": object_types,
              "val_names": [],
              "act_name": "event_activity",
              "time_name": "event_timestamp",
              "sep": ","}
ocel_gen = ocel_import_factory_csv.apply(file_path='../src/data/VAE_generated/gen_data_order.csv', parameters=parameters)

In [9]:
generalization = VAE_generalization(ocel_gen, ocpn)

Precision of IM-discovered net: 0.7596857379053943
Fitness of IM-discovered net: 0.6684185734099811
VAE Generalization= 0.7111358087042355


# Happy Path Order

In [12]:
filename = "../src/data/jsonocel/order_process.jsonocel"
happy_path__ocel = get_happy_path_log(filename)
happy_path_ocpn = ocpn_discovery_factory.apply(happy_path__ocel, parameters={"debug": False})
train_log = sample_traces(ocel, happy_path_ocpn, 10000, save_path='../src/data/playout/happy_data_order.txt')

Generate the traces: 100%|██████████| 10000/10000 [00:00<00:00, 36261.54it/s]


In [13]:
timesteps_max, enc_tokens, characters, char2id, id2char, x, x_decoder = get_text_data(num_samples=10000,
                                                                                      data_path='../src/data/playout/happy_data_order.txt')

print(x.shape, "Creating model...")

Number of samples: 10000
Number of unique input tokens: 15
Max sequence length for inputs: 18
(10000, 18, 15) Creating model...


In [14]:
input_dim, timesteps = x.shape[-1], x.shape[-2]
batch_size, latent_dim = 1, 191
intermediate_dim, epochs = 353, 10

vae, enc, gen, stepper = create_lstm_vae(input_dim,
                                         batch_size=batch_size,
                                         intermediate_dim=intermediate_dim,
                                         latent_dim=latent_dim,
                                        )
print("Training model...")

vae.fit([x, x_decoder], x, epochs=epochs, verbose=1)

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, None, 15)]   0           []                               
                                                                                                  
 lstm (LSTM)                    (None, 353)          521028      ['input_1[0][0]']                
                                                                                                  
 dense (Dense)                  (None, 191)          67614       ['lstm[0][0]']                   
                                                                                                  
 dense_1 (Dense)                (None, 191)          67614       ['lstm[0][0]']                   
                                                                                              

In [15]:
print("Fitted, predicting...")

def decode(s):
    return decode_sequence(s, gen, stepper, input_dim, char2id, id2char, timesteps_max)

log = []

for _ in tqdm(range(10000), desc="Sample Traces"):

    id_from = np.random.randint(0, x.shape[0] - 1)
    id_to = np.random.randint(0, x.shape[0] - 1)

    m_from, std_from = enc.predict([[x[id_from]]])
    m_to, std_to = enc.predict([[x[id_to]]])

    seq_from = np.random.normal(size=(latent_dim,))
    seq_from = m_from + std_from * seq_from

    seq_to = np.random.normal(size=(latent_dim,))
    seq_to = m_to + std_to * seq_to

    print("==  \t", " ".join([id2char[j] for j in np.argmax(x[id_from], axis=1)]), "==")

    for v in np.linspace(0, 1, 7):
        print("%.2f\t" % (1 - v), decode(v * seq_to + (1 - v) * seq_from))

    print("==  \t", " ".join([id2char[j] for j in np.argmax(x[id_to], axis=1)]), "==")
    parts = " ".join([id2char[j] for j in np.argmax(x[id_to], axis=1)]).split(' <end>')
    log.append([parts[0]])

Fitted, predicting...


Sample Traces:   0%|          | 0/10000 [00:00<?, ?it/s]

==  	 place order confirm order pay order pick item load cargo fuel car start route end route <end> 	 ==


Sample Traces:   0%|          | 4/10000 [00:01<36:52,  4.52it/s]  

1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pick item pay order load cargo fuel car start route end route <end> 	 ==
==  	 place order confirm order pick item load cargo pay order fuel car start route end route <end> 	 ==
1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pay order pick item load cargo fuel car start route end route <end> 	 ==
==  	 place order confirm order pick item load cargo pay order fuel car start route end route <end> 	 ==
1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place o

...

0.00	 place order confirm 
==  	 place order confirm order pay order pick item load cargo fuel car start route end route <end> 	 ==
==  	 place order confirm order pick item load cargo fuel car pay order start route end route <end> 	 ==
1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pay order pick item load cargo fuel car start route end route <end> 	 ==
==  	 place order confirm order pay order pick item load cargo fuel car start route end route <end> 	 ==
1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pick item load cargo fuel car start route end route pay order <end> 	 ==
==  	 place order confirm order pay order pick item load cargo fuel ca

Sample Traces: 100%|█████████▉| 9998/10000 [08:06<00:00, 22.16it/s]

0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pick item load cargo pay order fuel car start route end route <end> 	 ==
==  	 place order confirm order pay order pick item load cargo fuel car start route end route <end> 	 ==
1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pick item pay order load cargo fuel car start route end route <end> 	 ==
==  	 place order confirm order pick item load cargo fuel car start route pay order end route <end> 	 ==
1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pay orde

Sample Traces: 100%|██████████| 10000/10000 [08:06<00:00, 20.54it/s]

==  	 place order confirm order pick item load cargo pay order fuel car start route end route <end> 	 ==
1.00	 place order confirm 
0.83	 place order confirm 
0.67	 place order confirm 
0.50	 place order confirm 
0.33	 place order confirm 
0.17	 place order confirm 
0.00	 place order confirm 
==  	 place order confirm order pay order pick item load cargo fuel car start route end route <end> 	 ==


In [16]:
log

[['place order confirm order pick item pay order load cargo fuel car start route end route'],
 ['place order confirm order pay order pick item load cargo fuel car start route end route'],
 ['place order confirm order pay order pick item load cargo fuel car start route end route'],
 ['place order confirm order pay order pick item load cargo fuel car start route end route'],
 ['place order confirm order pick item pay order load cargo fuel car start route end route'],
 ['place order confirm order pick item pay order load cargo fuel car start route end route'],
 ['place order confirm order pay order pick item load cargo fuel car start route end route'],
 ['place order confirm order pay order pick item load cargo fuel car start route end route'],
 ['place order confirm order pay order pick item load cargo fuel car start route end route'],
 ['place order confirm order pick item pay order load cargo fuel car start route end route'],
 ['place order confirm order pay order pick item load cargo 

In [17]:
df_log = process_log(log, happy_path__ocel, happy_path_ocpn, '../src/data/VAE_generated/gen_data_order_happy.csv')

In [18]:
df_log

event_id event_activity  event_execution             event_timestamp  \
0             0    Place Order                1  2022-01-01 15:17:02.184014   
1             1  Confirm Order                1  2022-01-01 15:18:02.184014   
2             2      Pick Item                1  2022-01-01 15:19:02.184014   
3             3      Pay Order                1  2022-01-01 15:20:02.184014   
4             4     Load Cargo                1  2022-01-01 15:21:02.184014   
...         ...            ...              ...                         ...   
79995     79995      Pick Item            10000  2024-03-11 19:03:58.845322   
79996     79996     Load Cargo            10000  2024-03-11 19:04:58.845322   
79997     79997       Fuel Car            10000  2024-03-11 19:05:58.845322   
79998     79998    Start Route            10000  2024-03-11 19:06:58.845322   
79999     79999      End Route            10000  2024-03-11 19:07:58.845322   

              delivery     order         item  
0                   []  [order1]      [item1]  
1                   []  [order1]      [item1]  
2                   []        []      [item1]  
3                   []  [order1]           []  
4          [delivery1]        []      [item1]  
...                ...       ...          ...  
79995               []        []  [item10000]  
79996  [delivery10000]        []  [item10000]  
79997  [delivery10000]        []           []  
79998  [delivery10000]        []  [item10000]  
79999  [delivery10000]        []  [item10000]  

[80000 rows x 7 columns]

In [19]:
object_types = ["order","item","delivery"]
parameters = {"obj_names": object_types,
              "val_names": [],
              "act_name": "event_activity",
              "time_name": "event_timestamp",
              "sep": ","}
ocel_gen = ocel_import_factory_csv.apply(file_path='../src/data/VAE_generated/gen_data_order_happy.csv', parameters=parameters)

In [21]:
generalization = VAE_generalization(ocel_gen, happy_path_ocpn)

Precision of IM-discovered net: 0.75
Fitness of IM-discovered net: 1.0
VAE Generalization= 0.8571428571428571


# Flower Model Order

In [22]:
filename = "../src/data/jsonocel/order_process.jsonocel"
ots = ["order","item","delivery"]
flower_ocpn = create_flower_model(filename,ots)
train_log = sample_traces(ocel, flower_ocpn, 10000, save_path='../src/data/playout/flower_data_order.txt')

Generate the traces: 100%|██████████| 10000/10000 [00:16<00:00, 608.64it/s]


In [23]:
timesteps_max, enc_tokens, characters, char2id, id2char, x, x_decoder = get_text_data(num_samples=10000,
                                                                                      data_path='../src/data/playout/flower_data_order.txt')

print(x.shape, "Creating model...")

Number of samples: 10000
Number of unique input tokens: 21
Max sequence length for inputs: 70
(10000, 70, 21) Creating model...


In [24]:
input_dim, timesteps = x.shape[-1], x.shape[-2]
batch_size, latent_dim = 1, 191
intermediate_dim, epochs = 353, 10

vae, enc, gen, stepper = create_lstm_vae(input_dim,
                                         batch_size=batch_size,
                                         intermediate_dim=intermediate_dim,
                                         latent_dim=latent_dim,
                                        )
print("Training model...")

vae.fit([x, x_decoder], x, epochs=epochs, verbose=1)

Model: "model_4"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_6 (InputLayer)           [(None, None, 21)]   0           []                               
                                                                                                  
 lstm_2 (LSTM)                  (None, 353)          529500      ['input_6[0][0]']                
                                                                                                  
 dense_4 (Dense)                (None, 191)          67614       ['lstm_2[0][0]']                 
                                                                                                  
 dense_5 (Dense)                (None, 191)          67614       ['lstm_2[0][0]']                 
                                                                                            

KeyboardInterrupt: 

In [ ]:
print("Fitted, predicting...")

def decode(s):
    return decode_sequence(s, gen, stepper, input_dim, char2id, id2char, timesteps_max)

log = []

for _ in tqdm(range(10000), desc="Sample Traces"):

    id_from = np.random.randint(0, x.shape[0] - 1)
    id_to = np.random.randint(0, x.shape[0] - 1)

    m_from, std_from = enc.predict([[x[id_from]]])
    m_to, std_to = enc.predict([[x[id_to]]])

    seq_from = np.random.normal(size=(latent_dim,))
    seq_from = m_from + std_from * seq_from

    seq_to = np.random.normal(size=(latent_dim,))
    seq_to = m_to + std_to * seq_to

    print("==  \t", " ".join([id2char[j] for j in np.argmax(x[id_from], axis=1)]), "==")

    for v in np.linspace(0, 1, 7):
        print("%.2f\t" % (1 - v), decode(v * seq_to + (1 - v) * seq_from))

    print("==  \t", " ".join([id2char[j] for j in np.argmax(x[id_to], axis=1)]), "==")
    parts = " ".join([id2char[j] for j in np.argmax(x[id_to], axis=1)]).split(' <end>')
    log.append([parts[0]])

In [ ]:
log

In [ ]:
df_log = process_log(log, ocel, flower_ocpn, '../src/data/VAE_generated/gen_data_order_flower.csv')

In [ ]:
df_log

In [ ]:
object_types = ["order","item","delivery"]
parameters = {"obj_names": object_types,
              "val_names": [],
              "act_name": "event_activity",
              "time_name": "event_timestamp",
              "sep": ","}
ocel_gen = ocel_import_factory_csv.apply(file_path='../src/data/VAE_generated/gen_data_order_flower.csv', parameters=parameters)

In [ ]:
generalization = VAE_generalization(ocel_gen, flower_ocpn)